In [1]:
import pandas as pd
import ipywidgets
from branca import colormap as cm
import folium
from folium import FeatureGroup
from folium import plugins

In [ ]:
pd.options.display.max_colwidth = 30
pd.options.display.max_columns = None

# Documentation

In [2]:
from IPython.display import IFrame
Folium = IFrame(src='https://python-visualization.github.io/folium/', width=1000, height=500)
display(Folium)

In [3]:
from IPython.display import IFrame
Branca = IFrame(src='https://python-visualization.github.io/branca/index.html', width=1000, height=500)
display(Branca)

# Dataset
* Dataset/Done/restaurants.csv

# Display on Map

### Get Data

In [4]:
file = "Dataset/Done/restaurants.csv"
city = "Portland"

df = pd.read_csv(file)
df = df[df["city"]==city]
display(df.head())

business_id                           name  \
1   tCbdrRPZA0oiIYSmHG3J0w        Flying Elephants at PDX   
13  jx91IMdGOmLOo8h_F9z39g  Cleary's Restaurant & Spirits   
18  5PsApTz-WqhF_-8mfqGtGw                     Cafe Yumm!   
33  HMXiuCxHDXqMH1hBpaHd9g             Whole Time Chicken   
34  ZA3u0Nu5V6TqkcYh8U0zdg          B Street Coffee House   

                address      city state postal_code   latitude   longitude  \
1   7000 NE Airport Way  Portland    OR       97218  45.588906 -122.593331   
13   12429 NE Glisan St  Portland    OR       97230  45.526473 -122.535323   
18   301 SW Morrison St  Portland    OR       97204  45.518450 -122.675723   
33                  NaN  Portland    OR       97215  45.516241 -122.597527   
34   2190 W Burnside St  Portland    OR       97210  45.523074 -122.696206   

    stars  review_count  is_open                     attributes  \
1     4.0           126        1  {'RestaurantsTakeOut': 'Tr...   
13    3.5            19        1  {'RestaurantsGoodForGroups...   
18    3.5           158        1  {'OutdoorSeating': 'True',...   
33    5.0             7        0  {'OutdoorSeating': 'True',...   
34    4.5           131        0  {'Caters': 'False', 'Resta...   

                       categories                          hours  
1   Salad, Soup, Sandwiches, D...  {'Monday': '5:0-18:0', 'Tu...  
13  Nightlife, Sandwiches, Sea...  {'Monday': '7:0-23:0', 'Tu...  
18  Vegetarian, Vegan, Sandwic...  {'Monday': '10:0-17:0', 'T...  
33  Food Stands, Restaurants, ...  {'Monday': '11:0-20:0', 'T...  
34  Restaurants, Food, Sandwic...  {'Monday': '6:30-15:0', 'T...

### Create Map

#### Color Map

In [5]:
branca.colormap.LinearColormap?

Object `branca.colormap.LinearColormap` not found.


In [6]:
colorScale = cm.linear.YlOrRd_06.scale(1, 5)

colorMap1 = colorScale.to_step(index=[1, 1.5, 2, 2.5, 3, 3.5, 4, 4.5, 5])
colorMap1.caption = 'Indicate the average star of the restaurants'

colorMap2 = cm.LinearColormap(colors=["#003060", "#4B0091", "#005AB5", "#6F00D2", "#AE00AE", "#F00078", "#FFA042", "#FFD306", "#FFFF37"], index=[1, 1.5, 2, 2.5, 3, 3.5, 4, 4.5, 5], vmin=1, vmax=5)
colorMap2.caption = 'Indicate the average stars of the restaurants'

display(colorScale)
display(colorMap1)
display(colorMap2)

#### Scatter Map

In [7]:
folium.Circle?

In [16]:
# Portland
location = [45.50565889504914, -122.67878270710042]
category = "Brunch"

In [17]:
map = folium.Map(location=location, tiles='Open Street Map', zoom_start=11, control_scale=True)

Positron = folium.raster_layers.TileLayer('CartoDB Positron').add_to(map)
Dark_Matter = folium.raster_layers.TileLayer('CartoDB Dark_Matter').add_to(map)

plugins.Fullscreen(position='topleft').add_to(map)
plugins.MiniMap(toggle_display=True).add_to(map)
colorMap2.add_to(map)


for row in df.itertuples():
    if category in row.categories: 
        lat = row.latitude
        lng = row.longitude
        tooltip = row.name +'<br>' + str(row.address) +'<br>' + str(row.stars)
        popup = row.name +'<br>' + str(row.address) +'<br>' + str(row.stars)
        color = colorMap2(row.stars)

        folium.Circle(location=[lat, lng],
                      layer=map,
                      radius=5,
                      tooltip=tooltip,
    #                   popup=folium.Popup(popup, max_width=200), 
                      color=color, 
                      fill=True,
                      opacity=1,
                      fill_opacity=1).add_to(map)
        
        
folium.LayerControl(position='bottomleft').add_to(map)

map

#### Cluster Map

In [9]:
folium.Marker?

In [10]:
location = [45.50565889504914, -122.67878270710042]

map = folium.Map(location=location, zoom_start=10, control_scale=True)

plugins.Fullscreen(position='topleft').add_to(map)
plugins.MiniMap(toggle_display=True).add_to(map)
markerCluster = plugins.MarkerCluster().add_to(map)

for row in df.itertuples():
    lat = row.latitude
    lng = row.longitude
    tooltip = row.name +'<br>' + str(row.address) +'<br>' + str(row.stars)
    icon = "cutlery"
    
    folium.Marker(location=[lat, lng], 
                  tooltip=tooltip,
                  icon=folium.Icon(icon=icon)).add_to(markerCluster)

map

### Save Map

In [11]:
map.save("map.html")